In [1]:
# Import packages
import pandas as pd
import numpy as np
import datetime
import os


# Plot packages
from plotly.subplots import make_subplots
import plotly.graph_objects as go
import chart_studio.plotly as py
import cufflinks as cf
import seaborn as sns
import matplotlib.pyplot as plt
cf.go_offline()


# Data paths & parameters
BATH_PATH = os.getcwd()
DATA_PATH = os.path.join(BATH_PATH, "..", "data")
VRV_DATA_FILE = os.path.join(DATA_PATH, "VRV_Data.csv")
resample_step = "10min"

In [2]:
# Read Data
def get_VRV_data():
    vrv_data = pd.read_csv(VRV_DATA_FILE)
    vrv_data.set_index("DateTime", inplace=True)
    vrv_data.index = pd.to_datetime(vrv_data.index)
    return vrv_data
DF = get_VRV_data()
display(get_VRV_data())

VRV_02-RAT  VRV_02-TEMP_SP  VRV_02-KW  VRV_02-WD  \
DateTime                                                                
2022-08-01 00:00:00       26.40            25.0       0.09        5.0   
2022-08-01 00:10:00       26.40            25.0       0.09        5.0   
2022-08-01 00:20:00       26.40            25.0       0.09        5.0   
2022-08-01 00:30:00       26.40            25.0       0.09        5.0   
2022-08-01 00:40:00       26.64            25.0       0.09        5.0   
...                         ...             ...        ...        ...   
2022-09-30 23:10:00       26.40            26.0       0.09        5.0   
2022-09-30 23:20:00       26.48            26.0       0.09        5.0   
2022-09-30 23:30:00       26.68            26.0       0.09        5.0   
2022-09-30 23:40:00       26.80            26.0       0.09        5.0   
2022-09-30 23:50:00       26.80            26.0       0.09        5.0   

                     VRV_02-Status    OAT     RH  
DateTime                                          
2022-08-01 00:00:00            0.0  27.90  85.00  
2022-08-01 00:10:00            0.0  27.93  84.33  
2022-08-01 00:20:00            0.0  27.97  83.67  
2022-08-01 00:30:00            0.0  28.00  83.00  
2022-08-01 00:40:00            0.0  28.03  82.33  
...                            ...    ...    ...  
2022-09-30 23:10:00            0.0  26.33  92.17  
2022-09-30 23:20:00            0.0  26.27  92.33  
2022-09-30 23:30:00            0.0  26.20  92.50  
2022-09-30 23:40:00            0.0  26.13  92.67  
2022-09-30 23:50:00            0.0  26.07  92.83  

[8784 rows x 7 columns]

In [3]:
# %%
def KW_Plot(VRV):
    DF = get_VRV_data()
    DF_b = DF[:"2022-08-22"]
    DF_a = DF["2022-08-23":]

    X = DF.index
    X_a = DF_a.index
    X_b = DF_b.index

    Y_to = DF.loc[:, "OAT"]
    Y_ts = DF.loc[:, F"{VRV}-TEMP_SP"]

    Y_kw_b = DF_b.loc[:, F"{VRV}-KW"]
    Y_kw_a = DF_a.loc[:, F"{VRV}-KW"]

    Y_kw_avg_b = round(Y_kw_b.mean(), 2)
    Y_kw_avg_a = round(Y_kw_a.mean(), 2)
    Y_kw_avg_delta = round((Y_kw_avg_b - Y_kw_avg_a) * 16, 2)
    Y_kw_avg_pct = round((Y_kw_avg_delta / (Y_kw_avg_b * 16)) * 100, 2)

    fig = make_subplots(
        rows=5, cols=1, 
        shared_xaxes=True, vertical_spacing=0.15,
        specs=[[{"rowspan": 2}], [{}], [{"rowspan": 2}], [{}], [{"rowspan": 1}]])
    fig.add_trace(go.Scatter(name="Outdoor Temp.", x=X, y=Y_to, mode="lines"), row=1, col=1)
    fig.add_trace(go.Scatter(name="VRV Temp. SP", x=X, y=Y_ts, mode="lines"), row=1, col=1)
    fig.add_trace(go.Scatter(name="Energy usage (Before)", x=X_b, y=Y_kw_b, mode="lines", line=dict(color="rgb(255, 153, 51)")), row=3, col=1)
    fig.add_trace(go.Scatter(name="Energy usage (After)", x=X_a, y=Y_kw_a, mode="lines", line=dict(color="rgb(64, 191, 128)")), row=3, col=1)
    
    fig.add_trace(go.Scatter(name="Energy usage_avg (Before)", x=X_b, y=[Y_kw_avg_b]*len(DF_b), mode="lines", line=dict(dash="dash", color="rgb(255, 102, 26)"), showlegend=False), row=3, col=1)
    fig.add_trace(go.Scatter(name="Energy usage_avg (After)", x=X_a, y=[Y_kw_avg_a]*len(DF_a), mode="lines", line=dict(dash="dash", color="rgb(0, 102, 0)"), showlegend=False), row=3, col=1)
    fig.add_annotation(
        xref="paper", yref="paper", x=0.08, y=0.6, 
        text=F"KW_avg (Before): {Y_kw_avg_b} (KW)", font=dict(size=14, color="rgba(255, 102, 26, 0.8)"),
        showarrow=False, yshift=0.1)
    fig.add_annotation(
        xref="paper", yref="paper", x=0.8, y=0.6,
        text=F"KW_avg (After): {Y_kw_avg_a} (KW)", font=dict(size=14, color="rgba(0, 102, 0, 0.8)"),
        showarrow=False, yshift=0.1)

    RATg_1 = F"{VRV}-Status"
    fig.add_trace(go.Bar(
            name="VRV-ON (Before)", 
            x=DF_b.index, 
            y=DF_b.loc[:, RATg_1],
            marker_color="rgba(255, 102, 26, 0.1)", marker_line_color="rgba(255, 102, 26, 0.1)"),
            row=5, col=1)

    fig.add_trace(go.Bar(
            name="VRV-ON (After)", 
            x=DF_a.index, 
            y=DF_a.loc[:, RATg_1],
            marker_color="rgba(0, 102, 0, 0.1)", marker_line_color="rgba(0, 102, 0, 0.1)"),
            row=5, col=1)

    fig.update_layout(
        title = dict(text=F"{VRV} AI Strategy Outcomes<br><span style='font-size:12'> (Avg. Energy-Saving: {Y_kw_avg_delta} (KWh); Energy-Saving Rate: {Y_kw_avg_pct} %)", x=0.07, y=0.95),
        xaxis1 = dict(
            showline=True, linewidth=1.2, linecolor="black",
            showticklabels=False, showgrid=True, gridcolor="rgba(230, 230, 230, 1)",
            rangeslider=dict(visible=False)),
        xaxis3 = dict(
            showline=True, linewidth=1.2, linecolor="black",
            showticklabels=False, showgrid=True, gridcolor="rgb(230, 230, 230)",
            rangeslider=dict(visible=False)),
        xaxis5 = dict(
            showline=True, linewidth=1.2, linecolor="black",
            showticklabels=True, showgrid=True, gridcolor="rgba(230, 230, 230, 1)",
            rangeslider=dict(visible=False)),
        yaxis1 = dict(
            title=dict(text="Temp. (<sup>o</sup>C)", font=dict(size=12), standoff=0),
            range=[20, 36], dtick=4,  
            showline=True, linewidth=1.2, linecolor="black",
            showgrid=True, gridcolor="rgba(230, 230, 230, 1)"),
        yaxis3 = dict(
            title=dict(text="Energy Usage (KW)", font=dict(size=12), standoff=0),
            range=[0, 12], dtick=4,  
            showline=True, linewidth=1.2, linecolor="black",
            zeroline=True, zerolinewidth=0.5, zerolinecolor="black",
            showgrid=True, gridcolor="rgb(230, 230, 230)"),
        yaxis5 = dict(
            title=dict(text="ON/OFF", font=dict(size=12), standoff=0),
            range=[0, 1], dtick=1,  
            showline=True, linewidth=1.2, linecolor="black",
            zeroline=True, zerolinewidth=0.5, zerolinecolor="black",
            showgrid=True, gridcolor="rgb(230, 230, 230)"),
        legend = dict(x=0.1, y=1.08, orientation="h", bordercolor="black", borderwidth=0.5, font=dict(size=10)),
        plot_bgcolor="white", width=1200, height=600)
    fig.show()
VRV = "VRV_02"
KW_Plot(VRV)

In [4]:
def plot_KW_Temp(VRV):
    VRV_data = get_VRV_data()
    RATg_1 = F"{VRV}-Status"
    RATg_2 = F"{VRV}-TEMP_SP"
    RATg_3 = F"{VRV}-RAT"
    RATg_4 = "OAT"
    RATg_5 = F"{VRV}-KW"
    before_data = VRV_data[VRV_data.index<=datetime.datetime(2022, 8, 22, 0, 0)]
    after_data = VRV_data[VRV_data.index>=datetime.datetime(2022, 8, 23, 0, 0)]

    before_KW_avg = before_data.loc[:, RATg_5].mean()
    after_KW_avg = after_data.loc[:, RATg_5].mean()

    fig = go.Figure()
    fig.add_trace(go.Scatter(
        name="before",
        x=before_data.loc[:, RATg_4],
        y=before_data.loc[:, RATg_5],
        mode="markers"))  
    fig.add_trace(go.Scatter(
        name="after",
        x=after_data.loc[:, RATg_4],
        y=after_data.loc[:, RATg_5],
        mode="markers"))  

    fig.add_trace(go.Scatter(
        name="before_avg",
        x=before_data.loc[:, RATg_4],
        y=[before_KW_avg] * len(before_data.loc[:, RATg_4]),
        mode="lines", line=dict(color="rgb(0, 89, 179)", dash="dash"))) 
    fig.add_trace(go.Scatter(
        name="after_avg",
        x=after_data.loc[:, RATg_4],
        y=[after_KW_avg] * len(after_data.loc[:, RATg_4]),
        mode="lines", line=dict(color="rgb(255, 92, 51)", dash="dash")))

    fig.add_annotation(
        xref="paper", yref="paper", x=0.02, y=0.5, 
        text=F"KW_avg (Before): <br>{round(before_KW_avg, 2)} (KW)", font=dict(size=10, color="rgba(0, 89, 179, 0.8)"),
        showarrow=False, yshift=0.1)
    fig.add_annotation(
        xref="paper", yref="paper", x=0.98, y=0.12,
        text=F"KW_avg (After): <br>{round(after_KW_avg, 2)} (KW)", font=dict(size=10, color="rgba(255, 92, 51, 0.8)"),
        showarrow=False, yshift=0.1)

    fig.update_layout(
        title = dict(text=F"{VRV} Energy Performance<br><span style='font-size:12'>", x=0.04, y=0.9),
        xaxis = dict(
            title=dict(text="Temp. (<sup>o</sup>C)", font=dict(size=12), standoff=0),
            showline=True, linewidth=1.2, linecolor="black",
            showticklabels=True, showgrid=True, gridcolor="rgba(230, 230, 230, 1)",
            rangeslider=dict(visible=False)),
        yaxis = dict(
            title=dict(text="Energy Usage (KW)", font=dict(size=12), standoff=0),
            showline=True, linewidth=1.2, linecolor="black",
            showgrid=True, gridcolor="rgba(230, 230, 230, 1)"),
        legend = dict(x=1.02, y=0.5, orientation="v", bordercolor="black", borderwidth=0.5, font=dict(size=8)),
        plot_bgcolor="white", width=800, height=500)  
    fig.show()
VRV = "VRV_02"
plot_KW_Temp(VRV)